In [1]:
import pandas as pd
import requests
from pandas.io.json import json_normalize
from geopy.geocoders import Nominatim
import folium # map rendering library

In [2]:
url = 'https://services2.arcgis.com/J4VMdGWiZXReffvo/arcgis/rest/services/CityLimits/FeatureServer/0/query?where=1%3D1&outFields=*&outSR=4326&f=json'
results = requests.get(url).json()
results

{'objectIdFieldName': 'FID',
 'uniqueIdField': {'name': 'FID', 'isSystemMaintained': True},
 'globalIdFieldName': 'GlobalID',
 'geometryProperties': {'shapeAreaFieldName': 'Shape__Area',
  'shapeLengthFieldName': 'Shape__Length',
  'units': 'esriMeters'},
 'geometryType': 'esriGeometryPolygon',
 'spatialReference': {'wkid': 4326, 'latestWkid': 4326},
 'fields': [{'name': 'FID',
   'type': 'esriFieldTypeOID',
   'alias': 'FID',
   'sqlType': 'sqlTypeInteger',
   'domain': None,
   'defaultValue': None},
  {'name': 'OBJECTID_1',
   'type': 'esriFieldTypeInteger',
   'alias': 'OBJECTID_1',
   'sqlType': 'sqlTypeInteger',
   'domain': None,
   'defaultValue': None},
  {'name': 'OBJECTID',
   'type': 'esriFieldTypeInteger',
   'alias': 'OBJECTID',
   'sqlType': 'sqlTypeInteger',
   'domain': None,
   'defaultValue': None},
  {'name': 'CITY_NM',
   'type': 'esriFieldTypeString',
   'alias': 'CITY_NM',
   'sqlType': 'sqlTypeNVarchar',
   'length': 40,
   'domain': None,
   'defaultValue': Non

In [3]:
#cities = results['features','City Name']
#df = pd.json_normalize(results,'features',['attributes','CityName'],errors='ignore')
#df.rename(columns={"type": "Type"})
#df.drop('attributes.OBJECTID', axis=1)
#df.head(10)
county_data = results['features']
county_data[0]

{'attributes': {'FID': 1,
  'OBJECTID_1': 1,
  'OBJECTID': 1,
  'CITY_NM': 'Blaine',
  'UGA_NM': 'Blaine UGA',
  'UGA_NM2': 'Blaine - Incorporated UGA',
  'COUNTY_NM': 'Whatcom',
  'GMA': 'yes',
  'FIPS_PLC': '06505',
  'INCORP': 'yes',
  'ORIGIN': 'Whatcom parcels, DOR city',
  'DATEMOD': 20131227,
  'Shape_Leng': 83631.697826,
  'Shape_Le_1': 83631.697826,
  'Shape_Le_2': 129120.62934,
  'Shape_Le_3': 59878.8878571,
  'OBJECTID_2': 1,
  'OBJECTID_3': 1,
  'CITY_NM_1': 'Blaine',
  'UGA_NM_1': 'Blaine UGA',
  'UGA_NM2_1': 'Blaine - Incorporated UGA',
  'COUNTY_NM_': 'Whatcom',
  'GMA_1': 'yes',
  'FIPS_PLC_1': '06505',
  'INCORP_1': 'yes',
  'ORIGIN_1': 'Whatcom parcels, DOR city',
  'DATEMOD_1': 20131227,
  'Shape_Le_4': 83631.697826,
  'Shape_Le_5': 83631.697826,
  'Shape_Le_6': 129120.62934,
  'Shape_Le_7': 59878.8878571,
  'ORIG_FID': 1,
  'POINT_X': -13662742.841,
  'POINT_Y': 6272357.6385,
  'Mercator_L': 6272357.63848,
  'Mercator_1': -13662742.841,
  'StatePlane': -122.73450717

In [4]:
column_names = ['City Name','County', 'Latitude', 'Longitude']
counties = pd.DataFrame(columns = column_names)

In [5]:
counties

Empty DataFrame
Columns: [City Name, County, Latitude, Longitude]
Index: []

In [6]:
for data in county_data:
    city_name = data['attributes']['CITY_NM'] 
    county = data['attributes']['COUNTY_NM']
    lat = data['attributes']['StatePla_1']
    lon = data['attributes']['StatePlane']
    
    counties = counties.append({'City Name':city_name,
                                'County': county,
                                'Latitude': lat,
                                'Longitude': lon}, ignore_index=True)

In [7]:
counties.sort_values(by = ['City Name'], inplace = True)
counties.reset_index(drop = True)

City Name        County   Latitude   Longitude
0          Aberdeen  Grays Harbor  46.976117 -123.809870
1    Airway Heights       Spokane  47.645849 -117.579228
2            Albion       Whitman  46.791653 -117.251139
3            Algona          King  47.281997 -122.250430
4            Almira       Lincoln  47.710544 -118.937096
..              ...           ...        ...         ...
283          Yacolt         Clark  45.865278 -122.406809
284          Yakima        Yakima  46.592506 -120.549388
285    Yarrow Point          King  47.646051 -122.218170
286            Yelm      Thurston  46.939771 -122.626363
287          Zillah        Yakima  46.408257 -120.272943

[288 rows x 4 columns]

Use geopy library to get the latitude and longitude values of Washington State.

In [8]:
address = 'Washington State'

geolocator = Nominatim(user_agent="wa_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Washington State are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Washington State are 47.2868352, -120.2126139.


In [9]:
print('The dataframe has {} counties and {} cities.'.format(
        len(counties['County'].unique()),
        len(counties['City Name'].unique())
    )
)

The dataframe has 39 counties and 281 cities.


In [10]:
# create map of Washington State using latitude and longitude values
map_waState = folium.Map(location=[latitude, longitude], zoom_start=7)

# add markers to map
for lat, lng, ciname, cou in zip(counties['Latitude'], counties['Longitude'], counties['City Name'], counties['County']):
    label = '{}'.format(ciname)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_waState)  
    
map_waState

In [11]:
snohomish_data = counties[counties['County'] == 'Snohomish'].reset_index(drop=True)
#snohomish_data.sort_values(by = ['City Name'], inplace = True)
snohomish_data.head(20)

City Name     County   Latitude   Longitude
0           Arlington  Snohomish  48.168741 -122.145098
1             Bothell  Snohomish  47.792296 -122.211375
2               Brier  Snohomish  47.792469 -122.273569
3          Darrington  Snohomish  48.254640 -121.603046
4             Edmonds  Snohomish  47.811287 -122.353208
5             Everett  Snohomish  47.950463 -122.220855
6            Gold Bar  Snohomish  47.856446 -121.692088
7       Granite Falls  Snohomish  48.087409 -121.970464
8               Index  Snohomish  47.821483 -121.555939
9        Lake Stevens  Snohomish  48.003001 -122.096194
10           Lynnwood  Snohomish  47.828513 -122.303287
11         Marysville  Snohomish  48.081245 -122.156034
12         Mill Creek  Snohomish  47.863197 -122.203661
13             Monroe  Snohomish  47.859372 -121.985387
14  Mountlake Terrace  Snohomish  47.792111 -122.307655
15           Mukilteo  Snohomish  47.909256 -122.303159
16          Snohomish  Snohomish  47.927838 -122.097608
17           Stanwood  Snohomish  48.244891 -122.342915
18             Sultan  Snohomish  47.870296 -121.804000
19            Woodway  Snohomish  47.790684 -122.384704

In [12]:
address = 'Snohomish county, WA'

geolocator = Nominatim(user_agent="wa_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Snohomish are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Snohomish are 48.0074736, -121.7304882.


In [13]:
map_snohomish = folium.Map(location=[latitude, longitude], zoom_start=7)

# add markers to map
for lat, lng, ciname, cou in zip(snohomish_data['Latitude'], snohomish_data['Longitude'], snohomish_data['City Name'], snohomish_data['County']):
    label = '{}'.format(ciname)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_snohomish)  
    
map_snohomish

Let's continue with Foursquare and enter credentials and version

In [14]:
CLIENT_ID = 'H3H0QKIA1PEXVHNAQYL0TORR5LSMS0Z1DTIKXGFRZVPOKOZP' # your Foursquare ID
CLIENT_SECRET = 'PAPZXJNY4IQVWV3BO23KIBQ0Y5USLZRMSJ43HAYO5DXSZ3C2' # your Foursquare Secret
VERSION = '20200708' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: H3H0QKIA1PEXVHNAQYL0TORR5LSMS0Z1DTIKXGFRZVPOKOZP
CLIENT_SECRET:PAPZXJNY4IQVWV3BO23KIBQ0Y5USLZRMSJ43HAYO5DXSZ3C2


In [40]:
snohomish_data.loc[16, 'City Name']

'Snohomish'

In [42]:
city_lat = snohomish_data.loc[16, 'Latitude'] # neighborhood latitude value
city_lon = snohomish_data.loc[16, 'Longitude'] # neighborhood longitude value

city_name = snohomish_data.loc[16, 'City Name'] # neighborhood name

print('Latitude and longitude values of {} city are {}, {}.'.format(city_name, 
                                                               city_lat, 
                                                               city_lon))

Latitude and longitude values of Snohomish city are 47.9278377091, -122.097608349.


In [45]:
LIMIT = 200 # limit of number of venues returned by Foursquare API

radius = 10000 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=H3H0QKIA1PEXVHNAQYL0TORR5LSMS0Z1DTIKXGFRZVPOKOZP&client_secret=PAPZXJNY4IQVWV3BO23KIBQ0Y5USLZRMSJ43HAYO5DXSZ3C2&v=20200708&ll=48.0074736,-121.7304882&radius=10000&limit=200'

In [46]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f08bb711582505d8ff92f11'},
 'response': {'headerLocation': 'Current map view',
  'headerFullLocation': 'Current map view',
  'headerLocationGranularity': 'unknown',
  'totalResults': 8,
  'suggestedBounds': {'ne': {'lat': 48.097473690000086,
    'lng': -121.59621685590254},
   'sw': {'lat': 47.91747350999991, 'lng': -121.86475954409745}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c02db6a0d0e0f4770c4019a',
       'name': 'Lake Twentytwo Trail',
       'location': {'address': 'Mountain Loop Hwy.',
        'lat': 48.076903358269085,
        'lng': -121.74586415290833,
        'labeledLatLngs': [{'label': 'display',
          'lat': 48.076903358269085,
          'lng': -121.74586415290833}],
        'distance': 7813,
        'post

In [47]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [48]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head(200)

name               categories        lat         lng
0       Lake Twentytwo Trail                    Trail  48.076903 -121.745864
1        Mt. Pilchuck Summit                 Mountain  48.057950 -121.797786
2             Lake Twentytwo                     Lake  48.064228 -121.763856
3         Heather Lake Trail                    Trail  48.082339 -121.774084
4  Mount Pilchuck State Park  State / Provincial Park  48.065760 -121.814418
5     Heather Lake Trailhead                    Trail  48.083233 -121.776960
6     Mt. Pilchuck Trailhead                    Trail  48.070287 -121.814804
7    Greider Lakes Trailhead                    Trail  47.973288 -121.612468

In [39]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

72 venues were returned by Foursquare.


In [72]:
def getNearbyVenues(names, latitudes, longitudes, radius=8000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City Name', 
                  'City Latitude', 
                  'City Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [74]:
# type your answer here

snohomish_venues = getNearbyVenues(names=snohomish_data['City Name'],
                                   latitudes=snohomish_data['Latitude'],
                                   longitudes=snohomish_data['Longitude']
                                  )


Arlington
Bothell
Brier
Darrington
Edmonds
Everett
Gold Bar
Granite Falls
Index
Lake Stevens
Lynnwood
Marysville
Mill Creek
Monroe
Mountlake Terrace
Mukilteo
Snohomish
Stanwood
Sultan
Woodway


In [75]:
print(snohomish_venues.shape)
snb = snohomish_venues[snohomish_venues['Venue Category'] == 'Brewery']

print(snb.shape)
snb.head(100)

(1440, 7)
(42, 7)


City Name  City Latitude  City Longitude  \
13            Arlington      48.168741     -122.145098   
22            Arlington      48.168741     -122.145098   
96            Arlington      48.168741     -122.145098   
127             Bothell      47.792296     -122.211375   
129             Bothell      47.792296     -122.211375   
141             Bothell      47.792296     -122.211375   
142             Bothell      47.792296     -122.211375   
209               Brier      47.792469     -122.273569   
214               Brier      47.792469     -122.273569   
219               Brier      47.792469     -122.273569   
225               Brier      47.792469     -122.273569   
313             Edmonds      47.811287     -122.353208   
379             Edmonds      47.811287     -122.353208   
384             Edmonds      47.811287     -122.353208   
446             Everett      47.950463     -122.220855   
453             Everett      47.950463     -122.220855   
466             Everett      47.950463     -122.220855   
480             Everett      47.950463     -122.220855   
505             Everett      47.950463     -122.220855   
587        Lake Stevens      48.003001     -122.096194   
714            Lynnwood      47.828513     -122.303287   
717            Lynnwood      47.828513     -122.303287   
718            Lynnwood      47.828513     -122.303287   
775          Marysville      48.081245     -122.156034   
904          Mill Creek      47.863197     -122.203661   
914          Mill Creek      47.863197     -122.203661   
960              Monroe      47.859372     -121.985387   
999   Mountlake Terrace      47.792111     -122.307655   
1001  Mountlake Terrace      47.792111     -122.307655   
1068  Mountlake Terrace      47.792111     -122.307655   
1086  Mountlake Terrace      47.792111     -122.307655   
1089  Mountlake Terrace      47.792111     -122.307655   
1112           Mukilteo      47.909256     -122.303159   
1122           Mukilteo      47.909256     -122.303159   
1150           Mukilteo      47.909256     -122.303159   
1151           Mukilteo      47.909256     -122.303159   
1197          Snohomish      47.927838     -122.097608   
1206          Snohomish      47.927838     -122.097608   
1331             Sultan      47.870296     -121.804000   
1349            Woodway      47.790684     -122.384704   
1414            Woodway      47.790684     -122.384704   
1416            Woodway      47.790684     -122.384704   

                                          Venue  Venue Latitude  \
13                    Whitewall Brewing Company       48.128195   
22                              Skookum Brewery       48.158907   
96                               210 Brewing CO       48.214500   
127                             9 Yards Brewery       47.756638   
129                               Cairn Brewing       47.757219   
141                          20 Corners Brewing       47.767934   
142                  Triplehorn Brewing Company       47.769264   
209               Hemlock State Brewing Company       47.784585   
214                        Diamond Knot Brewpub       47.787882   
219                             9 Yards Brewery       47.756638   
225                               Cairn Brewing       47.757219   
313                      Salish Sea Brewing Co.       47.809612   
379                        Diamond Knot Brewpub       47.787882   
384               Hemlock State Brewing Company       47.784585   
446                            At Large Brewing       47.980872   
453                            Crucible Brewing       47.910837   
466                           Middleton Brewing       47.910643   
480                 Scuttlebutt Brewing Company       48.000863   
505             Diamond Knot Brewery & Alehouse       47.948463   
587                     Sound To Summit Brewing       47.934339   
714                        Diamond Knot Brewpub       47.787882   
717                      Salish Sea Brewing C